In [3]:
import IPython.display as ipd
import matplotlib.pyplot as plt
import librosa.display
import time
import warnings; warnings.simplefilter('ignore')
import pandas as pd
import numpy as np
import youtube_dl
import librosa
import os
import re
import tensorflow as tf

from tensorflow.keras import optimizers
from tensorflow.keras.layers import Flatten, Dense
from tensorflow.keras.models import Sequential
from __future__ import unicode_literals
from os import path, listdir 
from os.path import isfile, join
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder

In [4]:
format_music  = '.wav'

In [5]:
def two_d_to_one(data):
    data['Chroma_stft_f'] = data['Chroma_stft'].apply(lambda x: x[0])
    data['Chroma_stft_s'] = data['Chroma_stft'].apply(lambda x: x[1])

    data['Flatness'] = data['Flatness'].apply(lambda x: x[0])

    data['Tempogram_f'] = data['Tempogram'].apply(lambda x: x[0])
    data['Tempogram_s'] = data['Tempogram'].apply(lambda x: x[1])

    data = data.drop(columns="Chroma_stft")
    data = data.drop(columns="Flatness")
    data = data.drop(columns="Tempogram")
    return data

In [6]:
def extract_features(data, mono):
    if mono:
        data['Chroma_stft'] = data['Librosa_song'].apply(lambda y : librosa.feature.chroma_stft(y = y, sr = 44100))
        data['Flatness'] = data['Librosa_song'].apply(lambda y :librosa.feature.spectral_flatness(y = y))
        data['Tonnetz'] = data['Librosa_song'].apply(lambda y :librosa.effects.harmonic(y = y))
        data['Tempogram'] = data['Librosa_song'].apply(lambda y:
            librosa.feature.tempogram(
                onset_envelope=librosa.onset.onset_strength(y = y, sr = 44100), 
                sr = 44100)
        )
        return data
    else:
        data['Chroma_stft_x'] = data['Librosa_song'].apply(lambda y : librosa.feature.chroma_stft(y = y[0], sr = 44100))
        data['Chroma_stft_y'] = data['Librosa_song'].apply(lambda y : librosa.feature.chroma_stft(y = y[1], sr = 44100))
        
        data['Flatness_x'] = data['Librosa_song'].apply(lambda y :librosa.feature.spectral_flatness(y = y[0]))
        data['Flatness_y'] = data['Librosa_song'].apply(lambda y :librosa.feature.spectral_flatness(y = y[1]))
        
        data['Tonnetz'] = data['Librosa_song'].apply(lambda y :np.array([librosa.effects.harmonic(y = y[0]),
                                                                           librosa.effects.harmonic(y = y[1])]
                                                                         ))
        data['Tempogram_x'] = data['Librosa_song'].apply(lambda y:
            librosa.feature.tempogram(
                onset_envelope=librosa.onset.onset_strength(y = y[0], sr = 44100), 
                sr = 44100)
        )
        data['Tempogram_y'] = data['Librosa_song'].apply(lambda y:
            librosa.feature.tempogram(
                onset_envelope=librosa.onset.onset_strength(y = y[1], sr = 44100), 
                sr = 44100)
        )
        return data

In [7]:
def create_music_album(mono):
    music_album = {}
    directories = [i for i in listdir("music/") if not i.startswith(".")]
    for songs_dir in directories:
        music_album[songs_dir] = []
        for song in listdir(f"music/{songs_dir}"):
            add = True
            if not song.startswith(".") and not song == 'song_list':
                audio_data = f'music/{songs_dir}/{song}'
                x , sr = librosa.load(audio_data, mono=mono, sr=44100)    #Cambiar a x , sr = librosa.load(audio_data, mono=False) para ver como afecta
                if mono:
                    part_song = divide_by_sec(x, sr)
                else:
                    if len(x) == 2:
                        p1 = divide_by_sec(x[0], sr)
                        p2 = divide_by_sec(x[1], sr)
                        part_song = np.array(list(zip(p1,p2)))
                    else:
                        add = False
                if add:
                    music_album[songs_dir].append(part_song)
    return music_album

In [8]:
def dataFrame_music(mono):
    music_album = create_music_album(mono)
    lista_songs = []
    for genero in music_album:
        for song in range(len(music_album[genero])):
            for part_songs in music_album[genero][song]:
                lista_songs.append([part_songs, genero])
            
    dfsongs = pd.DataFrame(np.array(lista_songs), columns=['Librosa_song', 'Genre'])
    dfsongs = extract_features(dfsongs, mono)
    if mono:
        dfsongs = two_d_to_one(dfsongs)
    return dfsongs

In [9]:
def clean_name(song_name):
    to_clean = [" (Audio Oficial)", " (Videoclip Oficial)", " , letra", " Letra", " (oficial audio)", " (Audio)", " LETRA", " (Letra)", " (Lyric Video)", " (Lyric Video Oficial)", ]
    for delete_part in to_clean:
        song_name = song_name.replace(delete_part, "")
    return song_name

In [10]:
def clean_all_directories():
    directories = [i for i in listdir("music/") if not i.startswith(".")]
    for type_music in directories:
        for song in listdir(f"music/{type_music}"):
            if song != "song_list" and not song.startswith("."):
                os.remove(f"music/{type_music}/{song}")

In [11]:
def divide_by_sec(audio, sr, seconds = 5):
    divided_audio = []
    for it in range(1, round(len(audio)/(seconds*sr)+1)):
        start = (it-1)*seconds*sr
        end = it*seconds*sr
        divided_audio.append(audio[start:end])
    return divided_audio

In [ ]:
music_album = {}
directories = [i for i in listdir("music/") if not i.startswith(".")]
for songs_dir in directories:
    music_album[songs_dir] = []
    for song in listdir(f"music/{songs_dir}"):
        add = True
        if not song.startswith(".") and not song == 'song_list':
            audio_data = f'music/{songs_dir}/{song}'
            x , sr = librosa.load(audio_data, mono=mono, sr=44100)    #Cambiar a x , sr = librosa.load(audio_data, mono=False) para ver como afecta
            if mono:
                part_song = divide_by_sec(x, sr)
            else:
                if len(x) == 2:
                    p1 = divide_by_sec(x[0], sr)
                    p2 = divide_by_sec(x[1], sr)
                    part_song = np.array(list(zip(p1,p2)))
                else:
                    add = False
            if add:
                music_album[songs_dir].append(part_song)

lista_songs = []
for genero in music_album:
    for song in range(len(music_album[genero])):
        for part_songs in music_album[genero][song]:
            lista_songs.append([part_songs, genero])

dfsongs = pd.DataFrame(np.array(lista_songs), columns=['Librosa_song', 'Genre'])
dfsongs = extract_features(dfsongs, mono)
if mono:
    dfsongs = two_d_to_one(dfsongs)

In [55]:
music_album = create_music_album(True)

In [63]:
music_album['hiphop'][0][0]

array([0.03756301, 0.05729746, 0.06404947, ..., 0.04182687, 0.06018247,
       0.07203788], dtype=float32)

In [ ]:
%%time
one_dim = dataFrame_music(True)
one_dim

In [ ]:
%%time
two_dim = dataFrame_music(False)
two_dim

In [ ]:
#clean_all_directories()

In [31]:
X_dummies = pd.get_dummies(one_dim, columns=['Genre'])
y = X_dummies[re.findall(r"Genre\w*", " ".join(X_dummies.columns))]
X_dummies = X_dummies.drop(columns=re.findall(r"Genre\w*", " ".join(X_dummies.columns)))

In [32]:
X_train, X_val, y_train, y_val = train_test_split(X_dummies, y, random_state=42)

In [33]:
def unified_data(dataFrame):
    index = []
    data = []
    for rows in dataFrame.iterrows():
        index.append(rows[0])
        unified_colums = []
        for column_data in rows[1].tolist():
            unified_colums.extend(np.array(column_data))
        data.append(np.array(unified_colums))
    return np.array(data)

In [34]:
def unified_result(dataFrame):
    index = []
    data = []
    for rows in dataFrame.iterrows():
        unified_colums = []
        for column_data in rows[1].tolist():
            unified_colums.append(np.array(column_data))
        data.append(np.array(unified_colums))
    return np.array(data)

In [35]:
X_train_unified = unified_data(X_train)
X_val_unified = unified_data(X_val)
y_train_unified = unified_result(y_train)
y_val_unified = unified_result(y_val)

In [36]:
X_train_unified.shape[1:]

(442724,)

In [80]:
X_train_unified, X_val_unified, y_train_unified, y_val_unified

([[0.01150842,
   0.010534222,
   0.014070176,
   0.016817072,
   0.01178439,
   -0.0040577147,
   -0.030463131,
   -0.060477205,
   -0.08686464,
   -0.106650874,
   -0.11761842,
   -0.11693047,
   -0.11041222,
   -0.094119884,
   -0.06372054,
   -0.02950738,
   0.004754156,
   0.037875704,
   0.06433598,
   0.08009665,
   0.08359784,
   0.07512069,
   0.05868126,
   0.04063849,
   0.02409334,
   0.0073918244,
   -0.008435685,
   -0.025407154,
   -0.04313455,
   -0.054293834,
   -0.05838087,
   -0.057176296,
   -0.05156216,
   -0.040810406,
   -0.030543175,
   -0.026904324,
   -0.028643245,
   -0.037054688,
   -0.04885158,
   -0.058710855,
   -0.06907116,
   -0.08053756,
   -0.08835458,
   -0.09385926,
   -0.09613536,
   -0.09064492,
   -0.08439755,
   -0.08035015,
   -0.07311128,
   -0.06396448,
   -0.05338938,
   -0.040951163,
   -0.02851881,
   -0.018547066,
   -0.012948985,
   -0.014620795,
   -0.031317737,
   -0.05974601,
   -0.09335499,
   -0.12818192,
   -0.15579097,
   -0.17384

In [81]:
len(X_train)

110

In [82]:
X_train.insert(loc=1 ,column='Unified_data', value=X_train_unified)
X_val["Unified_data"] = X_val_unified
y_train['Unified_result'] = y_train_unified
y_val['Unified_result'] = y_val_unified

In [83]:
X_train

Librosa_song  \
145  [0.01150842, 0.010534222, 0.014070176, 0.01681...   
42   [0.29745483, 0.33702087, 0.34806824, 0.3374328...   
16   [0.05921936, 0.052368164, 0.051696777, 0.05238...   
10   [0.07434082, 0.059036255, 0.055236816, 0.06384...   
115  [-0.027899323, -0.04683717, -0.077743575, -0.1...   
..                                                 ...   
71   [0.34423828, 0.28547668, 0.18800354, 0.1172943...   
106  [0.25837165, 0.2617795, 0.2690187, 0.27952915,...   
14   [-0.04788208, -0.04801941, -0.049591064, -0.05...   
92   [0.07875688, 0.07995112, 0.07992561, 0.0790422...   
102  [0.21766864, 0.21637088, 0.2185204, 0.22156025...   

                                          Unified_data  \
145  [0.01150842, 0.010534222, 0.014070176, 0.01681...   
42   [0.29745483, 0.33702087, 0.34806824, 0.3374328...   
16   [0.05921936, 0.052368164, 0.051696777, 0.05238...   
10   [0.07434082, 0.059036255, 0.055236816, 0.06384...   
115  [-0.027899323, -0.04683717, -0.077743575, -0.1...   
..                                                 ...   
71   [0.34423828, 0.28547668, 0.18800354, 0.1172943...   
106  [0.25837165, 0.2617795, 0.2690187, 0.27952915,...   
14   [-0.04788208, -0.04801941, -0.049591064, -0.05...   
92   [0.07875688, 0.07995112, 0.07992561, 0.0790422...   
102  [0.21766864, 0.21637088, 0.2185204, 0.22156025...   

                                               Tonnetz  \
145  [0.0069713793, 0.0051519736, 0.007319049, 0.00...   
42   [0.14833409, 0.15671174, 0.15573637, 0.1261105...   
16   [0.03494095, 0.032669675, 0.031128459, 0.03261...   
10   [0.031195771, 0.02544237, 0.021216827, 0.02702...   
115  [-0.037280183, -0.048053782, -0.06953126, -0.0...   
..                                                 ...   
71   [0.24657094, 0.21857893, 0.16630709, 0.1318526...   
106  [0.20775339, 0.20920607, 0.212714, 0.2171277, ...   
14   [-0.025861975, -0.02563653, -0.026768278, -0.0...   
92   [0.067177236, 0.067161806, 0.06665158, 0.06527...   
102  [0.1939047, 0.19301525, 0.19441052, 0.19685267...   

                                         Chroma_stft_f  \
145  [0.37813017, 0.30902857, 0.508541, 0.38922858,...   
42   [0.18383329, 0.20236799, 0.17706437, 0.1908401...   
16   [0.4756486, 0.3554692, 0.32269725, 0.33941323,...   
10   [0.89672875, 0.736062, 0.3763808, 0.4817512, 0...   
115  [0.76628023, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0...   
..                                                 ...   
71   [0.59900415, 0.41863343, 0.28511336, 0.2734369...   
106  [0.60320544, 0.49828494, 0.5408797, 0.53147644...   
14   [0.5189703, 0.29480246, 0.24754661, 0.25192, 0...   
92   [0.7956725, 1.0, 1.0, 1.0, 0.47344875, 1.0, 0....   
102  [0.41078824, 0.32058105, 0.46155888, 0.3778583...   

                                         Chroma_stft_s  \
145  [0.53544044, 0.5170994, 0.65364593, 0.44509077...   
42   [0.23699808, 0.17126824, 0.19728763, 0.2446569...   
16   [0.2517699, 0.1371097, 0.11043311, 0.11652008,...   
10   [0.8180168, 0.6892541, 0.24385037, 0.27431026,...   
115  [0.299232, 0.38884118, 0.33283585, 0.2666901, ...   
..                                                 ...   
71   [0.3147412, 0.27038896, 0.25898457, 0.24951981...   
106  [0.6576723, 0.8475302, 1.0, 1.0, 1.0, 1.0, 1.0...   
14   [0.5071045, 0.1334704, 0.10932816, 0.08576874,...   
92   [0.93763685, 0.91786367, 0.85461223, 0.9559735...   
102  [0.41057226, 0.3700264, 0.4164855, 0.3699031, ...   

                                           Tempogram_f  \
145  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
42   [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
16   [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
10   [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
115  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
..                                                 ...   
71   [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
106  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
14   [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,

In [84]:
X_train = X_train.drop(columns=['Librosa_song', 'Tonnetz', 'Chroma_stft_f', 'Chroma_stft_s', 'Tempogram_f', 'Tempogram_s'])
X_val = X_val.drop(columns=['Librosa_song', 'Tonnetz', 'Chroma_stft_f', 'Chroma_stft_s', 'Tempogram_f', 'Tempogram_s'])
y_train = y_train.drop(columns=['Genre_pop','Genre_rock'])
y_val = y_val.drop(columns=['Genre_pop','Genre_rock'])

In [91]:
X_train

Unified_data
145  [0.01150842, 0.010534222, 0.014070176, 0.01681...
42   [0.29745483, 0.33702087, 0.34806824, 0.3374328...
16   [0.05921936, 0.052368164, 0.051696777, 0.05238...
10   [0.07434082, 0.059036255, 0.055236816, 0.06384...
115  [-0.027899323, -0.04683717, -0.077743575, -0.1...
..                                                 ...
71   [0.34423828, 0.28547668, 0.18800354, 0.1172943...
106  [0.25837165, 0.2617795, 0.2690187, 0.27952915,...
14   [-0.04788208, -0.04801941, -0.049591064, -0.05...
92   [0.07875688, 0.07995112, 0.07992561, 0.0790422...
102  [0.21766864, 0.21637088, 0.2185204, 0.22156025...

[110 rows x 1 columns]

In [92]:
X_train.shape[1:]

(1,)

In [37]:
model = Sequential([
    Dense(512, activation="relu", input_shape = X_train_unified.shape[1:]),#X_train.values.shape[1:] ),
    Dense(1024, activation="relu"),
    Dense(1024, activation="relu"),
    Dense(1024, activation="relu"),
    Dense(1024, activation="relu"),
    Dense(1024, activation="relu"),
    Dense(2, activation="softmax")
])

In [38]:
optimizer = optimizers.Adam(learning_rate=0.0001)
model.compile(optimizer=optimizer,
              loss="categorical_crossentropy",
              metrics=["accuracy"])
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 512)               226675200 
_________________________________________________________________
dense_8 (Dense)              (None, 1024)              525312    
_________________________________________________________________
dense_9 (Dense)              (None, 1024)              1049600   
_________________________________________________________________
dense_10 (Dense)             (None, 1024)              1049600   
_________________________________________________________________
dense_11 (Dense)             (None, 1024)              1049600   
_________________________________________________________________
dense_12 (Dense)             (None, 1024)              1049600   
_________________________________________________________________
dense_13 (Dense)             (None, 2)                

In [39]:
y_train

Genre_pop  Genre_rock
11          1           0
65          0           1
28          1           0
69          0           1
9           1           0
..        ...         ...
20          1           0
60          0           1
71          0           1
14          1           0
51          0           1

[66 rows x 2 columns]

In [ ]:
for song in X_train_unified:
    for element in song:
        print(type(element))
        break
    break

In [27]:
y_train_unified

array([[0, 0, 1],
       [0, 1, 0],
       [1, 0, 0],
       [1, 0, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 0, 1],
       [0, 0, 1],
       [0, 0, 1],
       [1, 0, 0],
       [0, 1, 0],
       [0, 1, 0],
       [1, 0, 0],
       [0, 1, 0],
       [0, 1, 0],
       [1, 0, 0],
       [1, 0, 0],
       [1, 0, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 0, 1],
       [0, 1, 0],
       [1, 0, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 1, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 0, 1],
       [0, 0, 1],
       [1, 0, 0],
       [0, 1, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 1, 0],
       [1, 0, 0],
       [0, 0, 1],
       [0, 0, 1],
       [0, 1, 0],
       [1, 0, 0],
       [0, 1, 0],
       [0, 1, 0],
       [1, 0, 0],
       [0, 0, 1],
       [1, 0, 0],
       [0, 1, 0],
       [0, 1, 0],
       [0, 0, 1],
       [0, 1, 0],
       [0, 0, 1],
       [0, 0, 1],
       [0,

In [40]:
history = model.fit(X_train_unified, y_train_unified,
         validation_data=(X_val_unified, y_val_unified),
         epochs=100,
         verbose=1,
         batch_size=32)

Epoch 1/100
3/3 [==============================] - 7s 1s/step - loss: 0.6520 - accuracy: 0.6307 - val_loss: 0.6727 - val_accuracy: 0.5217
Epoch 2/100
3/3 [==============================] - 3s 937ms/step - loss: 0.5150 - accuracy: 0.6504 - val_loss: 0.6203 - val_accuracy: 0.5217
Epoch 3/100
3/3 [==============================] - 2s 726ms/step - loss: 0.3602 - accuracy: 0.6270 - val_loss: 0.5912 - val_accuracy: 0.7391
Epoch 4/100
3/3 [==============================] - 2s 636ms/step - loss: 0.2238 - accuracy: 1.0000 - val_loss: 0.6496 - val_accuracy: 0.6522
Epoch 5/100
3/3 [==============================] - 2s 601ms/step - loss: 0.1575 - accuracy: 1.0000 - val_loss: 0.6575 - val_accuracy: 0.6957
Epoch 6/100
3/3 [==============================] - 2s 544ms/step - loss: 0.0595 - accuracy: 1.0000 - val_loss: 0.6492 - val_accuracy: 0.6957
Epoch 7/100
3/3 [==============================] - 2s 586ms/step - loss: 0.0314 - accuracy: 1.0000 - val_loss: 0.7012 - val_accuracy: 0.6957
Epoch 8/100
3/3 

In [41]:
history

In [ ]:
video_info = youtube_dl.YoutubeDL().extract_info(url = 'https://youtu.be/ujNeHIo7oTE' ,download=False)
video_info['title'] = clean_name(video_info['title'])
filename = f"music/test/{video_info['title']}.mp3"
options={
    'format':'bestaudio/best',
    'keepvideo':False,
    'outtmpl':filename,
}

with youtube_dl.YoutubeDL(options) as ydl:
    ydl.download([video_info['webpage_url']])

print("Download complete... {}".format(filename))

In [ ]:
music_album = {}
mono = True
songs_dir = 'test'
directories = [i for i in listdir("music/") if not i.startswith(".")]
music_album[songs_dir] = {}
for song in listdir(f"music/test"):
    add = True
    music_album[songs_dir] = []
    if not song.startswith(".") and not song == 'song_list':
        audio_data = f'music/{songs_dir}/{song}'
        x , sr = librosa.load(audio_data, mono=True, sr=44100)    #Cambiar a x , sr = librosa.load(audio_data, mono=False) para ver como afecta
        if mono:
            part_song = divide_by_sec(x, sr)
        else:
            if len(x) == 2:
                p1 = divide_by_sec(x[0], sr)
                p2 = divide_by_sec(x[1], sr)
                part_song = np.array(list(zip(p1,p2)))
            else:
                add = False
        if add:
            music_album[songs_dir].append(part_song)
music_album
lista_songs = []
for genero in music_album:
    for part_songs in music_album[genero][0]:
        lista_songs.append([part_songs, genero])

    dfsongs = pd.DataFrame(np.array(lista_songs), columns=['Librosa_song', 'Genre'])
    dfsongs = extract_features(dfsongs, mono)
    if mono:
        dfsongs = two_d_to_one(dfsongs)
dfsongs

In [ ]:
music_album

In [ ]:
dfsongs = dfsongs.drop(columns=["Genre"])
dfsongs

In [ ]:
test = unified_data(dfsongs)
test

In [ ]:
from tensorflow.keras.metrics import mean_squared_error as mse

In [ ]:
y_pred = model.predict(test)
np.mean(mse(y_pred,y_test))

## Correccion de los nombres de las canciones
A continuacion vamos a comprobar el nombre de las canciones que se van a descargar y vamos a introducir las partes del nombre que queremos borrar a la lista `to_clean` de la funcion `clean_name`. Asi, el nombre de las canciones será el correcto

In [ ]:
directories = [i for i in listdir("music/") if not i.startswith(".")]
for type_music in directories:
    f = open(f"music/{type_music}/song_list", "r")
    for song in f.readlines():
        video_info = youtube_dl.YoutubeDL().extract_info(url = song,download=False)
        print(f"{clean_name(video_info['title']) =}")

In [ ]:
directories = [i for i in listdir("music/") if not i.startswith(".")]
for type_music in directories:
    f = open(f"music/{type_music}/song_list", "r")
    for song in f.readlines():
        video_info = youtube_dl.YoutubeDL().extract_info(url = song,download=False)
        video_info['title'] = clean_name(video_info['title'])
        if not os.path.exists(f'music/{type_music}/{video_info["title"]}.mp3'):
            filename = f"music/{type_music}/{video_info['title']}.mp3"
            options={
                'format':'bestaudio/best',
                'keepvideo':False,
                'outtmpl':filename,
            }

            with youtube_dl.YoutubeDL(options) as ydl:
                ydl.download([video_info['webpage_url']])

            print("Download complete... {}".format(filename))
        time.sleep(15)

In [ ]:
music_album = {}
directories = [i for i in listdir("music/") if not i.startswith(".")]
for songs_dir in directories:
    music_album[songs_dir] = {}
    for song in listdir(f"music/{songs_dir}"):
        music_album[songs_dir] = []
        if not song.startswith(".") and not song == 'song_list':
            audio_data = f'music/{songs_dir}/{song}'
            x , sr = librosa.load(audio_data, mono=True, sr=44100)    #Cambiar a x , sr = librosa.load(audio_data, mono=False) para ver como afecta
            part_song = divide_by_sec(x, sr)
            music_album[songs_dir].append(part_song)


lista_songs = []
for genero in music_album:
    for part_songs in music_album[genero][0]:
        lista_songs.append([part_songs, genero])

    dfsongs = pd.DataFrame(np.array(lista_songs), columns=['Librosa_song', 'Genre'])
    dfsongs = extract_features(dfsongs, mono)
    if mono:
        dfsongs = two_d_to_one(dfsongs)
dfsongs

In [39]:
audio_data = 'music/hiphop/hiphop.00000.wav'
x , sr = librosa.load(audio_data, mono=False, sr=44100)

In [40]:
x , sr

(array([-0.16259822, -0.12736398, -0.02819149, ..., -0.00102521,
        -0.02031166, -0.01466712], dtype=float32),
 44100)

In [41]:
len(x)

1323008

In [ ]:
import soundfile as sf
sf.write('test.wav', z[-1], 44100)

In [ ]:
audio_data = 'test.wav'
ipd.Audio(audio_data)

In [42]:
ipd.Audio(audio_data)

In [ ]:
for genero in music_album:
    for name_song in music_album[genero]:
        plt.figure(figsize=(14, 5))
        librosa.display.waveplot(music_album[genero][name_song][0], sr=music_album[genero][name_song][1])
        titulo = genero+" -> "+name_song
        plt.title(titulo)
        plt.show()

In [ ]:
music_album['pop']['Marlon - Bajé de la Luna ft. Dani Martín.mp3'][0]

In [ ]:
lista_songs = []
for genero in music_album:
    for part_songs in music_album[genero][0]:
        lista_songs.append([part_songs, genero])

dfsongs = pd.DataFrame(np.array(lista_songs), columns=['Librosa_song', 'Genre'])

In [ ]:
dfsongs

In [ ]:
dfsongs['Chroma_stft'] = dfsongs['Librosa_song'].apply(chr_stft)
dfsongs['Flatness'] = dfsongs['Librosa_song'].apply(flatness)
dfsongs['Tonnetz'] = dfsongs['Librosa_song'].apply(tonnetz)
dfsongs['Tempogram'] = dfsongs['Librosa_song'].apply(tempogram)

In [ ]:
dfsongs

In [ ]:
dfsongs_one_d = pd.DataFrame(data=dfsongs.values, columns=dfsongs.columns)

dfsongs_one_d['Chroma_stft_f'] = dfsongs_one_d['Chroma_stft'].apply(lambda x: x[0])
dfsongs_one_d['Chroma_stft_s'] = dfsongs_one_d['Chroma_stft'].apply(lambda x: x[1])

dfsongs_one_d['Flatness'] = dfsongs_one_d['Flatness'].apply(lambda x: x[0])

dfsongs_one_d['Tempogram_f'] = dfsongs_one_d['Tempogram'].apply(lambda x: x[0])
dfsongs_one_d['Tempogram_s'] = dfsongs_one_d['Tempogram'].apply(lambda x: x[1])

dfsongs_one_d = dfsongs_one_d.drop(columns="Chroma_stft")
dfsongs_one_d = dfsongs_one_d.drop(columns="Flatness")
dfsongs_one_d = dfsongs_one_d.drop(columns="Tempogram")

dfsongs_one_d

In [ ]:
y = dfsongs['Genre']
X = dfsongs.drop(columns=['Name', 'Genre'])


In [ ]:
X.describe()

In [ ]:
X['Chroma_stft'][0]

In [ ]:
'''
X['Chroma_stft_1'] = X['Chroma_stft'].apply(lambda x: x[0])
X['Chroma_stft_2'] = X['Chroma_stft'].apply(lambda x: x[1])

X['Flatness_1'] = X['Flatness'].apply(lambda x: x[0])
X['Flatness_2'] = X['Flatness'].apply(lambda x: x[0])

X['Tempogram_1'] = X['Tempogram'].apply(lambda x: x[0])
X['Tempogram_2'] = X['Tempogram'].apply(lambda x: x[0])

X = X.drop(columns="Chroma_stft")
X = X.drop(columns="Flatness")
X = X.drop(columns="Tempogram")
'''

In [ ]:
type(X['Librosa_song'].values)

In [ ]:
import tensorflow as tf
from tensorflow.keras.layers import Flatten, Dense
from tensorflow.keras.models import Sequential

In [ ]:
X.head()

In [ ]:
for col in X.columns:
    new_X[col] = X[col].apply(lambda x: x.flatten())

In [ ]:
X_train, X_val, y_train, y_val =  train_test_split(X,y)

In [ ]:
X_train.shape

In [ ]:
len(X_train.values[0])

In [ ]:
pX_train = []
for rows in range(len(X_train)):
    aux = []
    for col in range(len(X_train.values[0])):
        aux.extend(X_train.values[rows][col])
    pX_train.append(aux)
pX_train

In [ ]:
model = Sequential([
    Dense(512, activation="tanh", input_shape = X_train.values.shape[1:] ),
    Dense(1024, activation="tanh"),
    Dense(1024, activation="tanh"),
    Dense(1024, activation="tanh"),
    Dense(1024, activation="tanh"),
    Dense(1024, activation="tanh"),
    Dense(2, activation="softmax")
])

In [ ]:
optimizer = keras.optimizers.Adam(learning_rate=0.0001)
model.compile(optimizer=optimizer,
              loss="categorical_crossentropy",
              metrics=["accuracy"])
model.summary()

In [ ]:
X_train

In [ ]:
len(X_train.values[:,:])

In [ ]:
X_train

In [ ]:
type(X_train)

In [ ]:
X_train.shape

In [ ]:
y_train

In [ ]:
model.fit(X_train, y_train.apply(lambda x: 0 if x=="rock" else 1),
         validation_data=(X_val, y_val.apply(lambda x: 0 if x=="rock" else 1)),
         epochs=100,
         batch_size=32)

In [ ]:
X_train.values

In [ ]:
nums = range(100)
impares = list(filter(lambda x: x%2, nums))
impares

In [ ]:
False == 0